# Pulumiを使用してカスタムアプリケーションをデプロイ

このノートブックでは、Pulumiを使用してカスタムアプリケーションをデプロイする方法の概要を説明します。


## 環境の初期化

環境を起動し、DataRobotライブラリをインポートします。続行する前に、このノートブックでタスクを実行するために[必要なアセットをダウンロード](https://s3.us-east-1.amazonaws.com/datarobot_public/drx/pulumi-minis/deploy_custom_app.zip)します。


In [1]:
import os
import datarobot as dr

os.environ['PULUMI_CONFIG_PASSPHRASE'] = 'default'

assert 'DATAROBOT_API_TOKEN' in os.environ, 'Please set the DATAROBOT_API_TOKEN environment variable'
assert 'DATAROBOT_ENDPOINT' in os.environ, 'Please set the DATAROBOT_ENDPOINT environment variable'

dr.Client()

## プロジェクトの設定

Pulumiスタックを作成または破棄する関数を設定します。


In [2]:
from pulumi import automation as auto


def stack_up(project_name: str, stack_name: str, program: callable) -> auto.Stack:
    # create (or select if one already exists) a stack that uses our inline program
    stack = auto.create_or_select_stack(
        stack_name=stack_name, project_name=project_name, program=program
    )

    stack.refresh(on_output=print)

    stack.up(on_output=print)
    return stack


def destroy_project(stack: auto.Stack):
    """Destroy pulumi project"""
    stack_name = stack.name
    stack.destroy(on_output=print)

    stack.workspace.remove_stack(stack_name)
    print(f"stack {stack_name} in project removed")

## 宣言型カスタムアプリケーションデプロイの作成

このセルを使用して、カスタムアプリケーションのデプロイを作成します。ソースコードをDataRobotに追加して、アプリケーションを初期化します。以下の`make_custom_application`関数は、これを宣言的に行う方法を示しています。すべてのアプリケーションテンプレートで、この関数のバリエーションを確認できます。


In [3]:
import pulumi_datarobot as datarobot
import pulumi


def make_custom_application():
    """Make a custom app on DataRobot.

    Upload source code to create source. Then initialize application.
    """

    file_mapping = [
        ("frontend/app.py", "app.py"),
        ("frontend/requirements.txt", "requirements.txt"),
        ("frontend/start-app.sh", "start-app.sh"),
    ]

    app_source = datarobot.ApplicationSource(
        resource_name="App Template Minis - Custom App Source",
        files=file_mapping,
        base_environment_id="6542cd582a9d3d51bf4ac71e",  # Python 3.9 streamlit environment
    )

    app = datarobot.CustomApplication(
        resource_name="App Template Minis - Custom App",
        source_version_id=app_source.version_id,
    )
    pulumi.export("Application Source Id", app_source.id)
    pulumi.export("Application Id", app.id)
    pulumi.export("Application Url", app.application_url)

## Pulumiスタックの実行

これで、Pulumiスタックを実行できます。そうすることで、ダウンロードしたアセットから`frontend`ディレクトリ内のファイルが取り出されて、DataRobotに配置され、アプリケーションが初期化されます。


In [ ]:
project_name = "AppTemplateMinis-CustomApplications"
stack_name = "MarshallsCustomApplicationDeployer"

stack = stack_up(project_name, stack_name, program=make_custom_application)

### 出力の操作

In [ ]:
import webbrowser

outputs = stack.outputs()
app_url = outputs.get("Application Url").value
webbrowser.open(app_url)

## 作業内容のクリア

アプリケーションを維持する必要がない場合もあります。このセルを使用してスタックをシャットダウンし、DataRobotで作成されたアセットを削除します。


In [ ]:
destroy_project(stack)